In [1]:
import exploration.option_trades as rvol
import datetime
import pandas as pd

from analytics import on_the_run
from scipy.interpolate import interp1d
from matplotlib import pyplot as plt
from ipywidgets import widgets

In [2]:
w = widgets.Dropdown(
    options=['IG', 'HY'],
    value='IG',
    description='Index:',
    disabled=False,
)
w

Dropdown(description='Index:', options=('IG', 'HY'), value='IG')

In [3]:
index = w.value
start_date=datetime.date(2014, 6, 11)
onTR, model = rvol.realized_vol(index, tenor="5yr", years=3)

In [4]:
onTR.plot()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [5]:
model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                     Constant Mean - GARCH Model Results                      
==============================================================================
Dep. Variable:          spread_return   R-squared:                      -0.001
Mean Model:             Constant Mean   Adj. R-squared:                 -0.001
Vol Model:                      GARCH   Log-Likelihood:                94.1921
Distribution:                  Normal   AIC:                          -180.384
Method:            Maximum Likelihood   BIC:                          -161.947
                                        No. Observations:                  742
Date:                Wed, Sep 11 2019   Df Residuals:                      738
Time:                        10:44:17   Df Model:                            4
                                  Mean Model                                  
==============================================================================
                 coef    std err          t      P>|t|        95.0% Conf. Int.
------------------------------------------------------------------------------
mu            -0.0178  7.408e-03     -2.400  1.641e-02 [-3.230e-02,-3.258e-03]
                              Volatility Model                              
============================================================================
                 coef    std err          t      P>|t|      95.0% Conf. Int.
----------------------------------------------------------------------------
omega      3.6040e-03  1.414e-03      2.548  1.082e-02 [8.322e-04,6.376e-03]
alpha[1]       0.1348  4.345e-02      3.103  1.914e-03   [4.968e-02,  0.220]
beta[1]        0.7960  5.441e-02     14.631  1.774e-48     [  0.689,  0.903]
============================================================================

Covariance estimator: robust
"""

In [6]:
#compute lo and hi percentiles of atm volatility daily change (vol of vol)
rvol.vol_var()

NameError: name 'df' is not defined

In [ ]:
df = rvol.atm_vol(index, start_date, moneyness = .2)
df['steepness'] = df.otm_vol - df.atm_vol
df1 = df.reset_index()
df1['date'] = df1.quotedate.dt.date
df1 = df1.groupby(['date','expiry']).last()
#Need to do: the vol looks jumpy, is it because of quote source issue? yes, need to first try to get the same quote source...

In [ ]:
r = []
time = [1/12, 2/12, 3/12, 4/12, 5/12]
for t in time:
    for date, g in df1.groupby(level='date'):
        f = interp1d(g['T'].values, g['steepness'].values, fill_value='extrapolate')
        r.append((date, t, f(t)))
steepness = pd.DataFrame(r, columns=['date', 'T', 'steepness'])
steepness = steepness.set_index(['date','T']).unstack().astype('float')
steepness.columns = steepness.columns.droplevel()
steepness.ewm(span = 3).mean().plot()

In [ ]:
(steepness.iloc[-1] - steepness.mean()) / steepness.std()

In [ ]:
#Need to do: look at steepness not on moneyness but on delta range (60 delta vs 20 delta)